# Zadání

V tělese GF($3^3$) s modulujícím ireducibilním polynomem $p=x^3+2x+2$ najděte inverzi k prvku $q=2x^2+x+2$.

## Rychlé řešení pomocí Sagemath

Nejprve prvočíselné těleso,

In [1]:
F=GF(3); F

Finite Field of size 3

pak okruh polynomů nad ním,

In [2]:
R.<x>=PolynomialRing(F); R

Univariate Polynomial Ring in x over Finite Field of size 3

Označíme si polynom, kterým budeme modulovat

In [3]:
p=R(x^3 + 2*x + 2); p

x^3 + 2*x + 2

A vytvoříme příslušné neprvočíslené těleso

In [4]:
K.<x> = GF(3**3, modulus=p); K

Finite Field in x of size 3^3

Polynom $q$ vytvoříme, jako prvek v tomto tělese, aby byla správně určena jeho inverze:

In [5]:
q=K(2*x^2+x+2); q

2*x^2 + x + 2

In [6]:
inv=q^(-1); inv

x^2 + x + 2

Ještě ověření:

In [7]:
q*inv

1

**Správný výsledek je $q^{-1}=x^2+x+2$.** 

Ještě srovnejte s tím, pokud je polynom $q$ uvažován jako prvek okruhu polynomů, neboli, pokud se nemoduluje polynomem $p$:


In [8]:
qpol=R(2*x^2+x+2); (qpol^(-1))

2/(x^2 + 2*x + 1)

Zde SageMath najde inverzi v takzvaném podílovém tělese (ale to je mimo rámec MPI). Co ale je v rámci látky MPI zcela evidentní je fakt, že $x^2+x+2$ jistě není **inverzí** polynomu $2x^2+x+2$ **v rámci okruhu polynomů**. V tomto okruhu totiž součin jistě není jedna. Bude to polynom čtvrtého stupně, jmenovitě:

In [9]:
R(x^2 + x + 2)*R(2*x^2 + x + 2)

2*x^4 + x^2 + x + 1


_____

## Postupné řešení pomocí EEA (též v Sagemath)


Nejprve vytvoříme okruh polynomů.

Nad rámec zadání zkontrolujeme ireducibilitu polynomu $p=x^3+2x+2$. Pro polynomy stupně nejvýše tři funguje jednoduché dosazovací kritérium. 

**Polynom stupně nejvýše tři se nedá rozložit, pokud žádný z prvků ze $\mathbb{Z}_3$ není jeho kořenem**
(polynom chápeme jako funkci z $\mathbb{Z}_3$ do $\mathbb{Z}_3$, neboli vše modulujeme třemi). Proto dosadíme všechny možné prvky z tělesa: 

In [10]:
p

x^3 + 2*x + 2

In [11]:
[p(z) for z in F]

[2, 2, 2]

Ani jednou nevyšla $0$, proto je polynom ireducibilní (v případě polynom stupně 4 a více, nelze udělat takto jednoduchý závěr!!!). 

Nyní postupně vytvoříme tabulku EEA se sloupci r,a,b,q. První dva řádky budou vypadat takto

| &nbsp; &nbsp; r(emainder) &nbsp; &nbsp;    | a - Bezout | b - Bezout | q(uotient) |
| ---  | --- | --- | --- |
| $x^3 + 2x + 2$  | 1 | 0 |  |
| $2x^2 + x + 2$  | 0 | 1 |  |

V tabulce bude na každém řádku platit 

$$
r=a\cdot p+b\cdot q
$$

EEA probíhá v okruhu polynomů, nikoliv v tělese GF($3^3$). To je důležité zejména na začátku, kdy dělíme se zbytkem $p/q$. Pokud bychom se pohybovali v tělese, tak by platilo, že $p\sim 0$ (je to modul) a $p/q\sim 0$. Čímž by algoritmus skončil. V tomto notebooku je $p$ prvkem okruhu a $q$ musíme předefinovat. Předpis bude stejný, ale bude to prvek jiného objektu, zde objektu "R" (nikoliv "K").

In [12]:
q=R(2*x^2+x+2); q


2*x^2 + x + 2

Nový řádek $i$ potom do tabulky doplňujeme podle následujícího klíče: Na pozice $q_i$ a $r_i$ zapíšeme částečný podíl a zbytek po dělení polynomů $r_{i-2}$ a $r_{i-1}$. Pozice $a_i$ a $b_i$ doplníme podle předpisu 

$$
a_{i+1}=a_{i-2}-q_i a_{i-1},\quad b_{i+1}=b_{i-2}-q_i b_{i-1}.
$$

Takto doplňujeme řádky až do momentu, kdy bude mít zbytek po dělení stupeň 1, neboli půjde o konstantní polynom.

In [13]:
r=[p,q]; qsl=[]; a=[1,0]; b=[0,1]; r,qsl,a,b,  

([x^3 + 2*x + 2, 2*x^2 + x + 2], [], [1, 0], [0, 1])

In [14]:
while (r[-1]).degree()>0:
    qi,ri=(r[-2]).quo_rem(r[-1])
    r.append(ri); qsl.append(qi)
    ai,bi = a[-2]-qi*a[-1], b[-2]-qi*b[-1]
    a.append(ai); b.append(bi)
    print (ri,ai,bi,qi)
    

(2*x + 1, 1, x + 1, 2*x + 2)
(2, 2*x, 2*x^2 + 2*x + 1, x)


Dostáváme

| r(emainder) --------   | a - Bezout --------| b - Bezout --------| q(uotient) --------|
| ---  | --- | --- | --- |
| $x^3 + 2x + 2$  | 1 | 0 |  |
| $2x^2 + x + 2$  | 0 | 1 |  |
|$2x + 1$| $1$| $x + 1$| $2x + 2$|
|$2$| $2x$| $2x^2 + 2x + 1$| $x$|

Obecně platí 
$$
r=a \cdot p + b \cdot q \qquad (\text{v} \mathbb{Z_3}[x]). 
$$

Po zmodulování obou stran polynomem $p$ dostáváme rovnost v GF($3^3$):
$$
r=b \cdot q \qquad  (\text{v GF} (3^3)) 
$$

**Z posledního řádku odečteme, že**
$$
2=(2x^2 + 2x + 1) \cdot q \qquad  (\text{v GF} (3^3)) 
$$
a po vynásobení inverzí $2^{-1}=2$
$$
2\cdot 2=2(2x^2 + 2x + 1) \cdot q \qquad (\text{v GF} (3^3)) 
$$
$$
1=(x^2 + x + 2) \cdot q \qquad (\text{v GF} (3^3)).
$$

**Inverzí k $q=2x^2+x+2$ je tedy $q^{-1}=x^2+x+2$.** 

________

### Poznámky k řešení

- Dělení polynomu polynomem se zbytkem zde nebylo vysvětleno, je třeba se naučit jinde.
- V neprvočíselném tělese nemusí vyjít jako zbytek na posledním řádku číslo 1. Zde vyšlo číslo 2. Vždy vyjde nenulová konstanta a pokud není rovna 1, je třeba provést přenásobení rovnice, která přísluší poslednímu řádku, tak jak to je ukázáno výše. Tento krok je kvalitativně jiný než iterace řádků, proto ho doporučuji provádět mimo tabulku.
- Pro úplnost a kvůli logice věci jsme vyčíslovali oba Bézoutovy koeficienty $a$ i $b$. K výpočtu inverze je ale třeba jen koeficient $b$. Zde je možné si ruční výpočet zjednodušit a sloupec $a$ zcela vynechat. 

# Formální polynomy

Při zjišťování ireducibility polynomu se hodí provést dosazení hodnot z tělesa a nalezení kořenů. Toto nám dává úplné kritérium u polynomů stupně nejvýše 3 a pomocné kritérium při vyšším stupni. Při dosazování se chováme k polynomu způsobem, který známe z analýzy, t.j. jako k funkci ze $\mathbb{Z}_3$ do $\mathbb{Z}_3$. Je to ale asi jediný moment, kdybychom si měli polynom takto představovat. A priori se jedná o formální polynomy. Jde vlastně o řetězce prvků z tělesa a na těchto řetězcích jsou definované operace, které se dobře vysvětlují pomocí známých operací na polynomech. 

**V teorii polynomů nad konečnými tělesy nemůžeme chápat polynom jako funkci.**

Pokud bychom chápali polynomy jako funkce, bylo by přirozené chápat je jako funkce z tělesa do tělesa, v tomto případě jako funkce ze $\mathbb{Z}_3$ do $\mathbb{Z}_3$. To by vedlo k problémům. Například - všech možných funkcí je $3^3=81$, kdežto polynomů různých stupňů je nekonečně mnoho. Dokonce už pro těleso GF($3^4$) potřebujeme více navzájem různých prvků.

S tím souvisí také to, že nad $\mathbb{Z}_3$ **jsou polynomy $p=x^3$ a $q=x$ různé**. Přitom v aritmetice $\mathbb{Z}_3$ platí $0^3=0$, $1^3=1$ a $2^3=2$, neboli by šlo o stejné objekty, pokud bychom je nesprávně chápali jako funkce.


Formálnost polynomů, jejich symbolickou podstatu budeme zdůrazňovat také tím, že budeme často mocniny proměnné $x$ ze zápisu vypouštět. například 

$$(x^2+2)\cdot(x+1)-x^3-x$$

budeme také zapisovat jako

$$102\cdot 11-1000-10=2121 \sim 2x^3+x^2+2x+1.$$